# Lesson 6 // APIs

In the last few notebooks we've been analyzing twitter data that was collected and collated for us. In this notebook we'll see how to gather Twitter data ourselves, using Twitter's APIs. In doing so we'll also learn the basics of gathering data more generally using APIs.

An API is an *Application Program Interface*, a way of accessing the functionality of a program from inside another program. APIs are software that act as intermediaries between two applications (in our context, a requester (you) and a website server). The API provides data in a standardized, efficient way, but first you need to know how to request things - APIs will differ in how this is done. You usually also need to get authorization to use the API beforehand.

R has some packages for interacting with some of the most commonly used APIs like twitter, facebook, etc. The **httr** package is a more general way of making *http* requests to an API and can be used in cases where there's no specialist package (if there is, it'll often be easier to use that than **httr**).

In the notebook we will:

1. Gather tweets and related data by searching against a sampling of recent tweets published in the past 7 days, using the **twitteR** package. The **twitteR** package provides an easy-to-use interface to the Twitter Search API.
2. Gather tweets directly from the twitter stream (rather than a sample), using the **streamR** package. The **streamR** package provides an interface to the Twitter Streaming API.
3. Show how you can do the same thing using the more general **httr** package, which is useful for cases where there is not a special purpose package for interacting with a particular API.


First load the required packages.

In [2]:
library(streamR)
library(twitteR)
library(tidyverse)
library(ggmap)
library(jsonlite)
library(httr)
library(stringr)

Loading required package: RCurl
Loading required package: bitops
Loading required package: rjson
Loading tidyverse: ggplot2
Loading tidyverse: tibble
Loading tidyverse: tidyr
Loading tidyverse: readr
Loading tidyverse: purrr
Loading tidyverse: dplyr
Conflicts with tidy packages ---------------------------------------------------
complete(): tidyr, RCurl
filter():   dplyr, stats
id():       dplyr, twitteR
lag():      dplyr, stats
location(): dplyr, twitteR

Attaching package: ‘jsonlite’

The following object is masked from ‘package:purrr’:

    flatten

The following objects are masked from ‘package:rjson’:

    fromJSON, toJSON



## Accessing the Twitter Search API using twitteR

Twitter Search API is part of Twitter’s REST API. It allows queries against the indices of recent or popular Tweets and behaves similarly to, but not exactly like the Search feature available in Twitter mobile or web clients, such as Twitter.com search. 

The Twitter Search API searches a sample of recent Tweets made in the last 7 days. When interpreting results its important to know that data collected in this way will not consist of *all* tweets (e.g. on a topic, by a user), just a sample of these. In other respects the Search API is similarly to using the search feature available on Twitter (e.g. see [Twitter.com](https://twitter.com/)).

Later on we will interface with Twitter Search API using **httr**. In this example, we're going to see how to interface with the API using the **twitteR** package. The results will be the same, and you could use either. The benefit of using **twitteR** is that it has been specifically designed of use with the Twitter Search API, and only that API, so it is a bit easier to use and you won't have to go wading through the API documentation. The **httr** package is more general, so it doesn't have e.g. functions that deal specifically with Twitter.

### Setting up a Twitter app

Many APIs require you to authenticate with OAuth tokens. OAuth is an open standard for token-based authentication on the Internet. Essentially, the Twitter API allows you to access various parts of Twitter's data resources. To use the API, Twitter needs to know who you are, and OAuth is the standard way of doing this. 

For the Twitter API, authentication is done through creating your own Twitter Application, which is linked to your Twitter account. Twitter grants the authentication token to your app, but since this is linked to your account it gives Twitter a way of tracing the requests back to you. The fact that we are setting up an "app" is not important - from our point-of-view this app will not do anything, it is just a way to tell Twitter who we are when we make requests for data.

So, we're now going to set up our own Twitter app and get the authentication details. 

The following instructions are adapted from [here](http://thinktostart.com/twitter-authentification-with-r/).

1. Go to https://apps.twitter.com/ and log in with your Twitter Account (you need a Twitter account to do this). Click the "Create new app" button.

2. Enter the details of your app on the screen that follows:
    + *Name*: this needs to be unique, so something like "test" won't be allowed, but other than that it doesn't matter what you call the app since you're the only person using it. 
    + *Description*: enter anything you want
    + *Website*: Enter any valid URL as the website (I use `http://www.stats.uct.ac.za/`). 
    + *Callback URL*: this is the only important bit! Enter `http://127.0.0.1:1410`. 
    + Tick the box that says you agree with the conditions of use.
    + Click the button that says "Create your twitter application".

3. You now need to get and write down your authentication details. 
    + Select the "Keys and Access Tokens" tab, 
    + Copy and paste the Consumer key (API key) and Consumer secret (API secret)
    + Click on "Create my access token" near the bottom of the page. Copy and paste the "Access Token" and "Access Token Secret". 

### Completing the OAuth authentication process in RStudio

1. Open up R/RStudio and load the **twitteR** package

2. Create variables for each of the authentication details you copied down previously. I save these to an .RData file for later use in the last line below but this is not really necessary (it just means I don't have to show you my authentication details in this notebook!). Remember not to share these details - they're passwords.
```
api_key <- "xxxxxxxxxxxxxx"
api_secret <- "xxxxxxxxxxxxxx"
access_token <- "xxxxxxxxxxxxxx-xxxxxxxxxxxxxx"
access_token_secret <- "xxxxxxxxxxxxxx"
save(api_key, api_secret, access_token, access_token_secret, file="my_twitteR_oauth.RData")
```
3. We now get OAuth authentication by passing the `setup_twitter_oauth()` function our `api_key` and `api_secret` from before (or by loading it again if saved as .RData i.e. `load(my_twitteR_oauth.RData)`).
```
setup_twitter_oauth(api_key,api_secret)
```
This will open up a web page that says "Authorize <YourTwitterAppName> to use your account?". Click "Authorize App" and return to R/RStudio. You should see a message "Authentication Complete". You're now done!

### Using twitteR to collect data

We need to start each session by providing our authentication details (you only need to create the OAuth token once, which we've done above, but you need to authenticate *every* twitteR session). 

In [3]:
# load authentication details into R (or just load api_key and api_secret as done above)
load("/Users/louwrenslabuschagne/Documents/MScDataScience/STA5073ZDataScienceForIndustry/classNotes/datasci-fi/data/my_twitteR_oauth.RData") 

# get OAuth authentication 
?setup_twitter_oauth
setup_twitter_oauth(api_key,api_secret)


[1] "Using browser based authentication"


Let's collect 100 tweets using the #GuptaLeaks hashtag:

In [4]:
# get some tweets
tweets <- searchTwitter('#GuptaLeaks', n=100)
str(tweets[[1]])

Reference class 'status' [package "twitteR"] with 17 fields
 $ text         : chr "RT @PoliticsL: Patiently waiting for the #Hawks and #NPA to take action over #GuptaLeaks #Corruption https://t.co/bjzrgjc6ps"
 $ favorited    : logi FALSE
 $ favoriteCount: num 0
 $ replyToSN    : chr(0) 
 $ created      : POSIXct[1:1], format: "2017-09-10 11:15:26"
 $ truncated    : logi FALSE
 $ replyToSID   : chr(0) 
 $ id           : chr "906838523277398016"
 $ replyToUID   : chr(0) 
 $ statusSource : chr "<a href=\"http://twitter.com/download/iphone\" rel=\"nofollow\">Twitter for iPhone</a>"
 $ screenName   : chr "GroenewaldPJ"
 $ retweetCount : num 11
 $ isRetweet    : logi TRUE
 $ retweeted    : logi FALSE
 $ longitude    : chr(0) 
 $ latitude     : chr(0) 
 $ urls         :'data.frame':	0 obs. of  4 variables:
  ..$ url         : chr(0) 
  ..$ expanded_url: chr(0) 
  ..$ dispaly_url : chr(0) 
  ..$ indices     : num(0) 
 and 53 methods, of which 39 are  possibly relevant:
   getCreated, getFavori

In [5]:
# view the data collected
head(tweets)

[[1]]
[1] "GroenewaldPJ: RT @PoliticsL: Patiently waiting for the #Hawks and #NPA to take action over #GuptaLeaks #Corruption https://t.co/bjzrgjc6ps"

[[2]]
[1] "Mohsin_Dasoo: RT @dailymaverick: .@amaBhungane &amp; Scorpio #GuptaLeaks: How Anoj Singh sang for his supper https://t.co/XdUBGrK7mt https://t.co/NzSnXxkEp1"

[[3]]
[1] "Mitchellm3: RT @PoliticsL: Patiently waiting for the #Hawks and #NPA to take action over #GuptaLeaks #Corruption https://t.co/bjzrgjc6ps"

[[4]]
[1] "Sveegdossantos: RT @Lean3JvV: Excellent read; \"Reason to Vote ANC\". This book is empty, just like the empty promises made by the ANC. #GuptaLeaks https://t…"

[[5]]
[1] "Matlho53: RT @PoliticsL: Patiently waiting for the #Hawks and #NPA to take action over #GuptaLeaks #Corruption https://t.co/bjzrgjc6ps"

[[6]]
[1] "ivan2meyer: RT @PoliticsL: Patiently waiting for the #Hawks and #NPA to take action over #GuptaLeaks #Corruption https://t.co/bjzrgjc6ps"


We can clean up the tweets by removing links and filtering out retweets, for example, using regular expressions.

In [6]:
# converts a list of objects from a single twitteR class and returns a data.frame
tweets_df <- twListToDF(tweets)

# clean up tweets
replace_reg <- "(https?:.*?([\\s]|[a-zA-Z0-9]$))|(www:.*?([\\s]|[a-zA-Z0-9]$))|&amp;|&lt;|&gt;|RT"
tweets_df <- tweets_df %>% as.tibble() %>%
  filter(!str_detect(text, "^RT")) %>%
  mutate(value = str_replace_all(text, replace_reg, ""))

tweets_df %>% select(value)
names(tweets_df)

value                                                                                                                                            
1  .@amaBhungane  Scorpio #GuptaLeaks: How Anoj Singh sang for his supper                                                                           
2  #BellPottinger role in #GuptaLeaks #StateCapture should be investigated by @metpoliceuk @RoryStewartUK…                                          
3  @MbalulaFikile @Julius_S_Malema It is as true as #Nkandla #waterklooflanding #guptaleaks with nobody getting charged or prosecuted.              
4  #GuptaLeaks \n#StateCapture \n#CountryDuty                                                                                                       
5  Patiently waiting for the #Hawks and #NPA to take action over #GuptaLeaks #Corruption                                                            
6  amaBhungane  Scorpio #GuptaLeaks: How #AnojSingh sang for his supper | Daily Maverick                                                            
7  @ewnreporter Zuma-Gupta fightback in full swing. Enabled by pathetic ANC. #GuptaLeaks                                                            
8  #HongKong: amaBhungane  Scorpio #GuptaLeaks: How Anoj Singh sang for his supper #NEWS                                                            
9  Do thank #Guptas #GuptaLeaks  #BellPottinger for #KMPG's disgraceful harboring of pungent biz ethics.\nStained  sh…                              
10 #bellpottinger #guptaleaks Is this another wedding/tax evasion/money laundering use of taxpayer money by Zuma and his bosses                     
11 @News24 Evidence in the #GuptaLeaks that points to guilt...they have cost us money, integrity and democracy and we…                              
12 BEFORE a few "do-gooders" in gilt-laden "PR" industry cry foul, do ���� a favour:\nREAD UP ON #GUPTALEAKS (then shut the F up).\n#BellPottinger��
13 @ewnreporter More attention than the #GuptaLeaks                                                                                                 
14 Wow... A bigger liar you will not meet. Check out the tell swallow at 6:37 in.. \n#GuptaLeaks\n#FatherOfDuduzaniMustGo                           
15 #GuptaLeaks #HurricaneIrma                                                                                                                       
16 @News24 Witch hunt/distraction tactics... Why ignore the more serious and evident issues regarding the Master's of…                              
17 #GuptaLeaks #Guptas #Trillan #ESKOM #Corruption #Accountability #CountryDuty                                                                     
18 amaBhungane  Scorpio #GuptaLeaks: How Anoj Singh sang for his supper | Daily Maverick                                                            
19 Gupta lawyers argue Bank of Baroda claim ;half-baked; #GuptaBank #Guptas #BankofBaroda…                                                          
20 Would you grant the interdict in the #GuptaBank case? #Guptas #BankofBaroda #StateCapture #GuptaLeaks                                            
21 .@amaBhungane  Scorpio #GuptaLeaks: How Anoj Singh sang for his supper                                                                           
22 #VIDEO The Bank of Baroda vs Guptas. Here's a quick explainer  #StateCapture #GuptaLeaks                                                         
23 @KPMG_SA please dont think 4 a second tht you are off the hook!! YOU NEED 2 ACCOUNT 2 SA 4  the wedding YOU felt like paying #GuptaLeaks         
24 #IJ Read: #Gupta Fake News Empire #GuptaLeaks                                                                                                    
25 #KPMG has lost credibility here. Public perception is that they cannot be trusted. #GuptaLeaks #Gupta                                            
26 #BellPottinger\n#zumamustfall\n#StateCapture\n#GuptaLeaks\n#GuptaEmails\n#FeesMustFall\n#SABC\n#Guptas\n#Zuma\n#ANC…          

[1] "text"          "favorited"     "favoriteCount" "replyToSN"    
 [5] "created"       "truncated"     "replyToSID"    "id"           
 [9] "replyToUID"    "statusSource"  "screenName"    "retweetCount" 
[13] "isRetweet"     "retweeted"     "longitude"     "latitude"     
[17] "value"

The data we collected doesn't just cover the text of the tweet. Twitter sends a whole lot of other information, including each user's location (a string the user enters when signing up for a twitter account). Here we extract the location strings and use the Google Maps API to try and find the approximate latitude and longitude of each user's location. 

In [7]:
# lookup user info
user_info <- lookupUsers(tweets_df$screenName)  
user_df <- twListToDF(user_info)  

# use google maps API to get lat/lon from given user location (one of the exercises!)
located_users <- !is.na(user_df$location)
locations <- geocode(user_df$location[located_users])  

Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=South%20Africa&sensor=false
Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=London,%20Cape%20Town%20&%20Jhb&sensor=false
Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=SA&sensor=false
Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=South%20Africa&sensor=false
Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=South%20Africa:%20Gauteng%20Province&sensor=false
Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=Somewhere%20with%20animals&sensor=false
Warning message:
“geocode failed with status ZERO_RESULTS, location = "Somewhere with animals"”Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=united%20kingdom&sensor=false
Information from URL : http://maps.googleapis.com/maps/api/geocode/json?address=Alberton,%20South%20Africa&s

We then plot this using **ggmap**, an extension to **ggplot2** to interface with Google Maps.

In [8]:
# plot tweets
qmplot(lon, lat, data = locations, geom="blank") +
  geom_point(data = locations, aes(x = lon, y = lat),
             colour = I("red"), shape = 1)

Using zoom = 3...
Map from URL : http://tile.stamen.com/toner-lite/3/1/2.png
Map from URL : http://tile.stamen.com/toner-lite/3/2/2.png
Map from URL : http://tile.stamen.com/toner-lite/3/3/2.png
Map from URL : http://tile.stamen.com/toner-lite/3/4/2.png
Map from URL : http://tile.stamen.com/toner-lite/3/5/2.png
Map from URL : http://tile.stamen.com/toner-lite/3/1/3.png
Map from URL : http://tile.stamen.com/toner-lite/3/2/3.png
Map from URL : http://tile.stamen.com/toner-lite/3/3/3.png
Map from URL : http://tile.stamen.com/toner-lite/3/4/3.png
Map from URL : http://tile.stamen.com/toner-lite/3/5/3.png
Map from URL : http://tile.stamen.com/toner-lite/3/1/4.png
Map from URL : http://tile.stamen.com/toner-lite/3/2/4.png
Map from URL : http://tile.stamen.com/toner-lite/3/3/4.png
Map from URL : http://tile.stamen.com/toner-lite/3/4/4.png
Map from URL : http://tile.stamen.com/toner-lite/3/5/4.png


ERROR: Error: GeomRasterAnn was built with an incompatible version of ggproto.
Please reinstall the package that provides this extension.


Below is a few more ways to use the `searchTwitter()` function, applying various filters to the search:

In [12]:
# filter by date
tweets <- searchTwitter('#GuptaLeaks', n=100, since='2017-08-23', until='2017-08-25')

Warning message in doRppAPICall("search/tweets", n, params = params, retryOnRateLimit = retryOnRateLimit, :
“100 tweets were requested but the API can only return 0”

list()

In [14]:
# filter by resultType (mixed [default], recent, popular)
tweets_rec <- searchTwitter('#GuptaLeaks', n=100, resultType = "recent")
tweets_pop <- searchTwitter('#GuptaLeaks', n=100, resultType = "mixed")

In [15]:
# filter by location

# constantia
tweets_con <- searchTwitter('#GuptaLeaks', n=100, geocode='-34.02273,18.44813,10mi')
# saxonwold
tweets_sax <- searchTwitter('#GuptaLeaks', n=100, geocode='-26.16058,28.04098,10mi')

## Accessing the Twitter Streaming API using streamR

The tweets that twitteR provides is based on a static snapshot of tweets that twitter provides, going back one week. An alternative way to use the twitter API is to use the **streamR** package to collect tweets through time.

You first need to create *another* twitter app and get authentication details. You do this in exactly the same way as before except that **you must leave the callback URL blank** (don't ask me why). Do that once, and save your Consumer key (API key), Consumer secret (API secret), Access token, and Access token secret. 

### Completing the OAuth authentication process in RStudio

1. Open up R/RStudio and load the **twitteR** package

2. Create variables for each of the authentication details you copied down previously
```
library(ROAuth)
api_key <- "xxxxxxxx"
api_secret <- "xxxxxxxx"
access_token <- "xxxxxxxxxxxxxx-xxxxxxxxxxxxxx"
access_token_secret <- "xxxxxxxxxxxxxx"
```
3. We now get OAuth authentication with the `OAuthFactory()` function. This is a bit more complicated that before but essentially we are still just passing `api_key` and `api_secret` to the function. 
```
my_oauth <- OAuthFactory$new(consumerKey = api_key, consumerSecret = api_secret, 
                             requestURL = "https://api.twitter.com/oauth/request_token", 
                             accessURL = "https://api.twitter.com/oauth/access_token", 
                             authURL = "https://api.twitter.com/oauth/authorize" )
my_oauth$handshake(cainfo = system.file("CurlSSL", "cacert.pem", package = "RCurl"))
save(my_oauth, file = "my_oauth.Rdata")
```

### Using streamR to collect data

As before we need to start each session by providing our authentication details (you would only do the previous parts *once*, but you need to do the bit below *every* session).

In [18]:
# load your OAuth token
load("/Users/louwrenslabuschagne/Documents/MScDataScience/STA5073ZDataScienceForIndustry/classNotes/datasci-fi/data/my_oauth.Rdata")

We capture tweets using the `filterStream()` function. There are various ways to use `filterStream()`. We can keep the stream open until we have collected a specified number of tweets, or for some time interval. It is also possible to follow certain people, or hashtags (see the help for details). Here we just show two uses.

In [26]:
# capture 10 tweets mentioning the "HurricaneHarvey" hashtag
filterStream(file.name="harvey_tweets.json",
              track="#HurricaneHarvey", tweets=10, oauth=my_oauth)

Capturing tweets...
Connection to Twitter stream was closed after 7 seconds with up to 10 tweets downloaded.


In [20]:
# capture tweets mentioning the "HurricaneHarvey" hashtag for 30s
filterStream(file="harvey_tweets.json",
              track="#HurricaneHarvey", timeout=30, oauth=my_oauth)

Capturing tweets...
Connection to Twitter stream was closed after 30 seconds with up to 12 tweets downloaded.


Parse the tweets to get them into a readable form (if you get an error, you may have no tweets!)

In [27]:
harvey_tweets <- readTweets(tweets="harvey_tweets.json")

Warning message in readLines(tweets, encoding = "UTF-8"):
“incomplete final line found on 'harvey_tweets.json'”

5 tweets have been parsed. 


We can view the text of the first tweet:

In [28]:
harvey_tweets[[1]]$text

[1] "RT @krbe: Big shouts to our girl @ddlovato for donating 50,000 bottles of water and $50,00 to #HurricaneHarvey relief! \xed\xa0\xbd\xed\xb8\x8d #NowPlaying 'No Pr…"

Below we extract all the tweet texts and store them in a new variable, with a call to `lapply`.

In [29]:
parsed_harvey <- lapply(harvey_tweets, FUN=`[[`, "text")

In [30]:
parsed_harvey

[[1]]
[1] "RT @krbe: Big shouts to our girl @ddlovato for donating 50,000 bottles of water and $50,00 to #HurricaneHarvey relief! \xed\xa0\xbd\xed\xb8\x8d #NowPlaying 'No Pr…"

[[2]]
[1] "RT @RedTRaccoon: All my bags are packed, I'm ready to go...\n\nI'm just waiting on deployment orders with @TeamRubicon to assist with… "

[[3]]
[1] "RT @Jarnocan: #jnj #donateaphoto #HurricaneHarvey #trumprussia #treason Russian agents bought ads promoting disgusting #fakenews… "

[[4]]
[1] "lol \xed\xa0\xbd\xed\xb8\x82\xed\xa0\xbd\xed\xb8\x82 https://t.co/olimHji0AF"

[[5]]
[1] "RT @Sustainable2050: Perhaps related to the fact that CO2-levels are now way higher than at any time during the last 800,000+ years. https:…"


## Accessing the Twitter Search API with httr

Where a special-purpose package like **twitteR** and **streamR** allows to to access an API, its almost definitely best to use it. But a limited number of these exist and so at some stage you might end up wanting to interact with an API for which an R package does not exist. 

In that case, you can use the more general **httr** package. Loosely speaking, **httr** is R's version of *HTTP* - the standard protocol used to send and receive files and other data over the web. HTTP (Hypertext Transfer Protocol) uses the client-server model: the HTTP client opens a connection and sends a message to an HTTP server requesting a resource. The HTTP server then sends a return message, usually with the requested resource.

The main **httr** (and, by extension, http) verbs are GET(), HEAD(), POST(), PATCH(), PUT() and DELETE(). We'll only deal with GET(), which is used to make a request.

In this example we send a request to the Twitter Search API using the **httr** package. If you have not already done so (see the first example), register an application at https://apps.twitter.com/ and replace key and secret below.

In [32]:
load("/Users/louwrenslabuschagne/Documents/MScDataScience/STA5073ZDataScienceForIndustry/classNotes/datasci-fi/data/my_twitteR_oauth.RData")

We now need to get an OAuth token "the **httr** way":

In [33]:
myapp <- oauth_app("twitter", key = api_key, secret = api_secret)
twitter_token <- oauth1.0_token(oauth_endpoints("twitter"), myapp)

Let's make a request for the Twitter Search API to return tweets associated with the hashtag "Hurricane Harvey".

In [37]:
harvey_tweets <- GET("https://api.twitter.com/1.1/search/tweets.json?q=%23tensorflow",
           config(token = twitter_token))

Of course to use the API effectively we need to know how to make requests. To find this out, you need to read the API documentation. For Twitter APIs the documentation is extensive; other APIs may well be much less so. Typically you would need to spend quite a bit of time familiarising yourself with an API you wanted to use.

The documentation for the Twitter Search API can be found [here](https://dev.twitter.com/rest/public/search). 

You'll see our search term "#HurricaneHarvey" has been encoded as "%23HurricaneHarvey" in the URL provided to `GET()`. To find the URL encoding you need you can either search for the term on Twitter and note the URL that comes up, or use an online URL encoder such as [this one](https://www.seocentro.com/tools/online/url-encoder.html).

Finally, the default is to return 15 results at a time, but that can be increased to a maximum of 100 with the addition of `&count=100` to the end of the query URL.

Let's get 50 tweets and examine what's in the response object.

In [40]:
harvey_tweets <- GET("https://api.twitter.com/1.1/search/tweets.json?q=%23Tensorflow&count=50",
           config(token = twitter_token))

In [41]:
str(content(harvey_tweets)) # also try str(harvey_tweets)

List of 2
 $ statuses       :List of 50
  ..$ :List of 26
  .. ..$ created_at               : chr "Sun Sep 10 12:48:32 +0000 2017"
  .. ..$ id                       : num 9.07e+17
  .. ..$ id_str                   : chr "906861950344339459"
  .. ..$ text                     : chr "RT @KirkDBorne: Building Convolutional Neural Networks with #Tensorflow: https://t.co/G1mp5tvaPx #abdsc #BigData #DataScience #"| __truncated__
  .. ..$ truncated                : logi FALSE
  .. ..$ entities                 :List of 4
  .. .. ..$ hashtags     :List of 4
  .. .. .. ..$ :List of 2
  .. .. .. .. ..$ text   : chr "Tensorflow"
  .. .. .. .. ..$ indices:List of 2
  .. .. .. .. .. ..$ : int 60
  .. .. .. .. .. ..$ : int 71
  .. .. .. ..$ :List of 2
  .. .. .. .. ..$ text   : chr "abdsc"
  .. .. .. .. ..$ indices:List of 2
  .. .. .. .. .. ..$ : int 97
  .. .. .. .. .. ..$ : int 103
  .. .. .. ..$ :List of 2
  .. .. .. .. ..$ text   : chr "BigData"
  .. .. .. .. ..$ indices:List of 2
  .. .. .. .. .

The response sent back by the Twitter server consists of three parts: 

1. the status line, 
2. the headers,
3. the body. 

The status line tells you the status of your request: 200 means everything is working fine, 404 means the resource you requested was not found. If you are accessing an API from within a function, you should strongly consider throwing a warning or raise an error if a request did not succeed, using `warn_for_status()` or `stop_for_status()`. 

In [42]:
status_code(harvey_tweets)
http_status(harvey_tweets)

[1] 200

$category
[1] "Success"

$reason
[1] "OK"

$message
[1] "Success: (200) OK"

Headers are used to pass additional information about the request. These are often things like operating parameters, like when the request was sent, the format of the response, etc. We won't be needing headers much (at all really), but just for completeness they're shown below.

In [43]:
headers(harvey_tweets)

$`cache-control`
[1] "no-cache, no-store, must-revalidate, pre-check=0, post-check=0"

$`content-disposition`
[1] "attachment; filename=json.json"

$`content-encoding`
[1] "gzip"

$`content-length`
[1] "29526"

$`content-type`
[1] "application/json;charset=utf-8"

$date
[1] "Sun, 10 Sep 2017 12:53:41 GMT"

$expires
[1] "Tue, 31 Mar 1981 05:00:00 GMT"

$`last-modified`
[1] "Sun, 10 Sep 2017 12:53:41 GMT"

$pragma
[1] "no-cache"

$server
[1] "tsa_f"

$status
[1] "200 OK"

$`strict-transport-security`
[1] "max-age=631138519"

$`x-access-level`
[1] "read"

$`x-connection-hash`
[1] "3e6ec846f5abd9b23094085ae3bb7aef"

$`x-content-type-options`
[1] "nosniff"

$`x-frame-options`
[1] "SAMEORIGIN"

$`x-rate-limit-limit`
[1] "180"

$`x-rate-limit-remaining`
[1] "175"

$`x-rate-limit-reset`
[1] "1505048716"

$`x-response-time`
[1] "338"

$`x-transaction`
[1] "00d727de00758409"

$`x-twitter-response-tags`
[1] "BouncerCompliant"

$`x-xss-protection`
[1] "1; mode=block"

attr(,"class")
[1] "insensitive" "list"

The body, as the name suggests, contains the meat of the request and this will be what we focus on. Depending on the format of the response, the body can be parsed in a number of ways using the `content()` function.

In [44]:
# parse as a character vector (doesn't parse nicely)
content(harvey_tweets, "text")

[1] "{\"statuses\":[{\"created_at\":\"Sun Sep 10 12:48:32 +0000 2017\",\"id\":906861950344339459,\"id_str\":\"906861950344339459\",\"text\":\"RT @KirkDBorne: Building Convolutional Neural Networks with #Tensorflow: https:\\/\\/t.co\\/G1mp5tvaPx #abdsc #BigData #DataScience #MachineLearn\\u2026\",\"truncated\":false,\"entities\":{\"hashtags\":[{\"text\":\"Tensorflow\",\"indices\":[60,71]},{\"text\":\"abdsc\",\"indices\":[97,103]},{\"text\":\"BigData\",\"indices\":[104,112]},{\"text\":\"DataScience\",\"indices\":[113,125]}],\"symbols\":[],\"user_mentions\":[{\"screen_name\":\"KirkDBorne\",\"name\":\"Kirk Borne\",\"id\":534563976,\"id_str\":\"534563976\",\"indices\":[3,14]}],\"urls\":[{\"url\":\"https:\\/\\/t.co\\/G1mp5tvaPx\",\"expanded_url\":\"http:\\/\\/bit.ly\\/2wRF3gV\",\"display_url\":\"bit.ly\\/2wRF3gV\",\"indices\":[73,96]}]},\"metadata\":{\"iso_language_code\":\"en\",\"result_type\":\"recent\"},\"source\":\"\\u003ca href=\\\"http:\\/\\/twitter.com\\/download\\/android\\\" rel=\\\"nofollow\\\"\\u003eTwitter for Android\\u003c\\/a\\u003e\",\"in_reply_to_status_id\":null,\"in_reply_to_status_id_str\":null,\"in_reply_to_user_id\":null,\"in_reply_to_user_id_str\":null,\"in_reply_to_screen_name\":null,\"user\":{\"id\":2336470682,\"id_str\":\"2336470682\",\"name\":\"Michael Akinwumi PhD\",\"screen_name\":\"datawumi\",\"location\":\"Edmonton, AB, CANADA\",\"description\":\"Underwriting Analytics | Risk Analytics | Marketing Analytics | Claims Analytics\",\"url\":null,\"entities\":{\"description\":{\"urls\":[]}},\"protected\":false,\"followers_count\":524,\"friends_count\":682,\"listed_count\":351,\"created_at\":\"Mon Feb 10 10:41:15 +0000 2014\",\"favourites_count\":181,\"utc_offset\":-21600,\"time_zone\":\"Mountain Time (US & Canada)\",\"geo_enabled\":true,\"verified\":false,\"statuses_count\":3495,\"lang\":\"en\",\"contributors_enabled\":false,\"is_translator\":false,\"is_translation_enabled\":false,\"profile_background_color\":\"ACDED6\",\"profile_background_image_url\":\"http:\\/\\/abs.twimg.com\\/images\\/themes\\/theme18\\/bg.gif\",\"profile_background_image_url_https\":\"https:\\/\\/abs.twimg.com\\/images\\/themes\\/theme18\\/bg.gif\",\"profile_background_tile\":false,\"profile_image_url\":\"http:\\/\\/pbs.twimg.com\\/profile_images\\/584547541833748482\\/SZnYMPTA_normal.jpg\",\"profile_image_url_https\":\"https:\\/\\/pbs.twimg.com\\/profile_images\\/584547541833748482\\/SZnYMPTA_normal.jpg\",\"profile_banner_url\":\"https:\\/\\/pbs.twimg.com\\/profile_banners\\/2336470682\\/1428203256\",\"profile_link_color\":\"038543\",\"profile_sidebar_border_color\":\"EEEEEE\",\"profile_sidebar_fill_color\":\"F6F6F6\",\"profile_text_color\":\"333333\",\"profile_use_background_image\":true,\"has_extended_profile\":false,\"default_profile\":false,\"default_profile_image\":false,\"following\":false,\"follow_request_sent\":false,\"notifications\":false,\"translator_type\":\"none\"},\"geo\":null,\"coordinates\":null,\"place\":null,\"contributors\":null,\"retweeted_status\":{\"created_at\":\"Sun Sep 10 03:52:33 +0000 2017\",\"id\":906727068205019136,\"id_str\":\"906727068205019136\",\"text\":\"Building Convolutional Neural Networks with #Tensorflow: https:\\/\\/t.co\\/G1mp5tvaPx #abdsc #BigData #DataScience\\u2026 https:\\/\\/t.co\\/fRctKiWrb6\",\"truncated\":true,\"entities\":{\"hashtags\":[{\"text\":\"Tensorflow\",\"indices\":[44,55]},{\"text\":\"abdsc\",\"indices\":[81,87]},{\"text\":\"BigData\",\"indices\":[88,96]},{\"text\":\"DataScience\",\"indices\":[97,109]}],\"symbols\":[],\"user_mentions\":[],\"urls\":[{\"url\":\"https:\\/\\/t.co\\/G1mp5tvaPx\",\"expanded_url\":\"http:\\/\\/bit.ly\\/2wRF3gV\",\"display_url\":\"bit.ly\\/2wRF3gV\",\"indices\":[57,80]},{\"url\":\"https:\\/\\/t.co\\/fRctKiWrb6\",\"expanded_url\":\"https:\\/\\/twitter.com\\/i\\/web\\/status\\/906727068205019136\",\"display_url\":\"twitter.com\\/i\\/web\\/status\\/9\\u2026\",\"indices\":[111,134]}]},\"metadata\":{\"iso_language_code\":\"en\",\"result_type\":\"recent\"},

In [45]:
# parse as a raw vector (even worse):
content(harvey_tweets, "raw")

    [1] 7b 22 73 74 61 74 75 73 65 73 22 3a 5b 7b 22 63 72 65 61 74 65 64 5f 61
   [25] 74 22 3a 22 53 75 6e 20 53 65 70 20 31 30 20 31 32 3a 34 38 3a 33 32 20
   [49] 2b 30 30 30 30 20 32 30 31 37 22 2c 22 69 64 22 3a 39 30 36 38 36 31 39
   [73] 35 30 33 34 34 33 33 39 34 35 39 2c 22 69 64 5f 73 74 72 22 3a 22 39 30
   [97] 36 38 36 31 39 35 30 33 34 34 33 33 39 34 35 39 22 2c 22 74 65 78 74 22
  [121] 3a 22 52 54 20 40 4b 69 72 6b 44 42 6f 72 6e 65 3a 20 42 75 69 6c 64 69
  [145] 6e 67 20 43 6f 6e 76 6f 6c 75 74 69 6f 6e 61 6c 20 4e 65 75 72 61 6c 20
  [169] 4e 65 74 77 6f 72 6b 73 20 77 69 74 68 20 23 54 65 6e 73 6f 72 66 6c 6f
  [193] 77 3a 20 68 74 74 70 73 3a 5c 2f 5c 2f 74 2e 63 6f 5c 2f 47 31 6d 70 35
  [217] 74 76 61 50 78 20 23 61 62 64 73 63 20 23 42 69 67 44 61 74 61 20 23 44
  [241] 61 74 61 53 63 69 65 6e 63 65 20 23 4d 61 63 68 69 6e 65 4c 65 61 72 6e
  [265] 5c 75 32 30 32 36 22 2c 22 74 72 75 6e 63 61 74 65 64 22 3a 66 61 6c 73
  [289] 65 2c 22 65 6e 74 69 74 69 65 73

In [46]:
# parse using default parsers provided by httr for common file types
content(harvey_tweets, "parsed")

$statuses
$statuses[[1]]
$statuses[[1]]$created_at
[1] "Sun Sep 10 12:48:32 +0000 2017"

$statuses[[1]]$id
[1] 9.06862e+17

$statuses[[1]]$id_str
[1] "906861950344339459"

$statuses[[1]]$text
[1] "RT @KirkDBorne: Building Convolutional Neural Networks with #Tensorflow: https://t.co/G1mp5tvaPx #abdsc #BigData #DataScience #MachineLearn…"

$statuses[[1]]$truncated
[1] FALSE

$statuses[[1]]$entities
$statuses[[1]]$entities$hashtags
$statuses[[1]]$entities$hashtags[[1]]
$statuses[[1]]$entities$hashtags[[1]]$text
[1] "Tensorflow"

$statuses[[1]]$entities$hashtags[[1]]$indices
$statuses[[1]]$entities$hashtags[[1]]$indices[[1]]
[1] 60

$statuses[[1]]$entities$hashtags[[1]]$indices[[2]]
[1] 71



$statuses[[1]]$entities$hashtags[[2]]
$statuses[[1]]$entities$hashtags[[2]]$text
[1] "abdsc"

$statuses[[1]]$entities$hashtags[[2]]$indices
$statuses[[1]]$entities$hashtags[[2]]$indices[[1]]
[1] 97

$statuses[[1]]$entities$hashtags[[2]]$indices[[2]]
[1] 103



$statuses[[1]]$entities$hashtags[[3]]
$st

We can also check the file type, verify that its JSON, and then use our own JSON parser.

In [47]:
# check file type 
http_type(harvey_tweets)

[1] "application/json"

In [48]:
# format is json so can parse ourselves using jsonlite package
parsed_harvey <- fromJSON(content(harvey_tweets, "text"), simplifyVector = TRUE)

Once the tweets have been parsed, we can easily extract the information that we want. For example, below we extract the text content of the tweets, and the date they were created.

In [57]:
parsed_harvey$statuses$entities

hashtags                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       
1  Tensorflow , abdsc      , BigData    , DataScience, 60         , 71         , 97         , 103        , 104        , 112        , 113        , 125                                                                                                                                                                                                                                                                                                                                                                                                                             
2  Keras     , TensorFlow, 24        , 30        , 33        , 44                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
3  TensorFlow, 22        , 33                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
4  TensorFlow    , DeepLearning  , NeuralNetworks, CNNs          , LSTMs         , RNNs          , 75            , 86            , 87            , 100           , 101           , 116           , 117           , 122           , 123           , 129           , 130           , 135                                                                                                                                                                                                                                                                                            
5  TensorFlow, 4         , 15                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
6  MachineLearning, Spark          , H20            , Singa          , Caffe2         , TensorFlow     , AWS            , Azure          , Veles          , mlpack2        , Neon           , 40             , 56             , 57             , 63             , 64             , 68             , 69             , 75             , 76             , 83             , 84             , 95             , 96             , 100            , 101            , 107            , 108            , 114            , 115            , 123            , 124            , 129            
7  MachineLearning, Spark          , H20            , Singa   

In [51]:
parsed_harvey$statuses$created_at

[1] "Sun Sep 10 12:48:32 +0000 2017" "Sun Sep 10 12:06:16 +0000 2017"
 [3] "Sun Sep 10 11:52:56 +0000 2017" "Sun Sep 10 11:51:16 +0000 2017"
 [5] "Sun Sep 10 11:49:36 +0000 2017" "Sun Sep 10 11:38:24 +0000 2017"
 [7] "Sun Sep 10 11:38:23 +0000 2017" "Sun Sep 10 11:32:44 +0000 2017"
 [9] "Sun Sep 10 11:31:46 +0000 2017" "Sun Sep 10 10:29:12 +0000 2017"
[11] "Sun Sep 10 10:29:11 +0000 2017" "Sun Sep 10 10:21:43 +0000 2017"
[13] "Sun Sep 10 10:01:39 +0000 2017" "Sun Sep 10 09:44:13 +0000 2017"
[15] "Sun Sep 10 09:44:02 +0000 2017" "Sun Sep 10 09:16:48 +0000 2017"
[17] "Sun Sep 10 09:10:45 +0000 2017" "Sun Sep 10 09:06:45 +0000 2017"
[19] "Sun Sep 10 09:06:45 +0000 2017" "Sun Sep 10 09:03:25 +0000 2017"
[21] "Sun Sep 10 08:57:35 +0000 2017" "Sun Sep 10 08:54:34 +0000 2017"
[23] "Sun Sep 10 08:38:25 +0000 2017" "Sun Sep 10 08:36:01 +0000 2017"
[25] "Sun Sep 10 08:35:44 +0000 2017" "Sun Sep 10 08:35:20 +0000 2017"
[27] "Sun Sep 10 08:35:04 +0000 2017" "Sun Sep 10 08:35:00 +0000 2017"
[29] "Sun Sep 10 08:16:10 +0000 2017" "Sun Sep 10 07:43:04 +0000 2017"
[31] "Sun Sep 10 07:42:11 +0000 2017" "Sun Sep 10 07:40:47 +0000 2017"
[33] "Sun Sep 10 07:17:10 +0000 2017" "Sun Sep 10 07:16:35 +0000 2017"
[35] "Sun Sep 10 07:13:25 +0000 2017" "Sun Sep 10 06:16:30 +0000 2017"
[37] "Sun Sep 10 06:11:22 +0000 2017" "Sun Sep 10 06:04:04 +0000 2017"
[39] "Sun Sep 10 06:04:04 +0000 2017" "Sun Sep 10 05:59:42 +0000 2017"
[41] "Sun Sep 10 05:58:59 +0000 2017" "Sun Sep 10 05:58:05 +0000 2017"
[43] "Sun Sep 10 05:48:26 +0000 2017" "Sun Sep 10 05:36:37 +0000 2017"
[45] "Sun Sep 10 05:33:37 +0000 2017" "Sun Sep 10 05:32:55 +0000 2017"
[47] "Sun Sep 10 05:24:06 +0000 2017" "Sun Sep 10 05:19:15 +0000 2017"
[49] "Sun Sep 10 05:16:40 +0000 2017" "Sun Sep 10 05:16:06 +0000 2017"

## Exercises

1. The **Quandl** package provides a way of accessing the [Quandl](https://www.quandl.com/) API, which houses various kinds of financial and economic data. Many datasets are free, but if you would like to make more than 50 calls to the API a day, you need to create a free Quandl account and get an API key. You can have a look at the available datasets at https://docs.quandl.com/docs/data-organization. Data is brought into with R with the `Quandl()` `Quandl.datatable command()`, for time-series and data table objects respectively. See what data is available and in what format at the link above. Now, (a) create a Quandl account and get an API key, (b) find the `WIKI/PRICES` dataset and use the Quandl API to extract end of day stock prices for Apple and Microsoft for the period 1/1/2016 to 31/12/2016. Plot these two time series.

2. Use the **httr** package to send a request to the Geolocation service of Google Maps JavaScript API that will give you the latitude-longitude co-ordinates of your home address.  The Geolocation service takes a street address (a string) and returns some data on that address (e.g. latitude and longitude). To find out what the form of the request should look consult the documentation [here](https://developers.google.com/maps/documentation/geocoding/start)).

3. Use the **httr** package and consult the [documentation](https://dev.twitter.com/rest/public/search) on how to extract the followers of a user from the Twitter Search API. Extract the followers for a user of your choice and plot a histogram of the locations of these followers. 